In [4]:

import requests
import pandas as pd
import numpy as np

from dotenv import load_dotenv
import os
import json
from pandas.io.json import json_normalize

import pandas as pd
from sklearn.preprocessing import RobustScaler
import numpy as np
import seaborn as sns
pd.reset_option('display.max_rows')



In [5]:
# Cargar el archivo .env
load_dotenv()

# Acceder al valor de una variable
api_key = os.getenv("API_KEY")

folder_path = "data/IRON/Final"


In [6]:
df_test = pd.read_json("data/IRON/Timeline/test.json")


In [7]:
df_test["metadata"]["matchId"]

'LA2_1308805366'

In [8]:
#Esto es para un archivo json

df = pd.read_json('data/IRON/Timeline/test.json')
df_loop = pd.DataFrame(df["info"]["frames"][15]["participantFrames"]).transpose()[["championStats", "damageStats", "jungleMinionsKilled", "minionsKilled", "totalGold", "xp"]].reset_index(drop=True)
#df_loop = df_loop.transpose().drop(columns=["championStats","currentGold","goldPerSecond","participantId","position","timeEnemySpentControlled","level"])
#df_loop.reset_index(drop=True, inplace=True)
damage_stats = df_loop["damageStats"]
champion_stats = df_loop["championStats"]
damage_stats_expanded = pd.json_normalize(damage_stats)
champion_stats_expanded = pd.json_normalize(champion_stats)
#df_completo = pd.concat([df_loop, damage_stats_expanded, champion_stats_expanded], axis=1)
damage_stats_expanded = damage_stats_expanded.reset_index(drop=True)
champion_stats_expanded = champion_stats_expanded.reset_index(drop=True)

combined_df = df_loop.join(champion_stats_expanded)
combined_df = combined_df.join(damage_stats_expanded).drop(columns=["championStats", "damageStats"])


df_loop

championStats  \
0  {'abilityHaste': 0, 'abilityPower': 15, 'armor...   
1  {'abilityHaste': 0, 'abilityPower': 0, 'armor'...   
2  {'abilityHaste': 0, 'abilityPower': 0, 'armor'...   
3  {'abilityHaste': 0, 'abilityPower': 20, 'armor...   
4  {'abilityHaste': 0, 'abilityPower': 53, 'armor...   
5  {'abilityHaste': 0, 'abilityPower': 0, 'armor'...   
6  {'abilityHaste': 0, 'abilityPower': 0, 'armor'...   
7  {'abilityHaste': 0, 'abilityPower': 80, 'armor...   
8  {'abilityHaste': 0, 'abilityPower': 0, 'armor'...   
9  {'abilityHaste': 0, 'abilityPower': 0, 'armor'...   

                                         damageStats jungleMinionsKilled  \
0  {'magicDamageDone': 29266, 'magicDamageDoneToC...                   0   
1  {'magicDamageDone': 21287, 'magicDamageDoneToC...                  69   
2  {'magicDamageDone': 3304, 'magicDamageDoneToCh...                   0   
3  {'magicDamageDone': 1576, 'magicDamageDoneToCh...                   4   
4  {'magicDamageDone': 5947, 'magicDamageDoneToCh...                   0   
5  {'magicDamageDone': 4200, 'magicDamageDoneToCh...                   0   
6  {'magicDamageDone': 21146, 'magicDamageDoneToC...                  76   
7  {'magicDamageDone': 42542, 'magicDamageDoneToC...                   1   
8  {'magicDamageDone': 138, 'magicDamageDoneToCha...                   0   
9  {'magicDamageDone': 0, 'magicDamageDoneToChamp...                   0   

  minionsKilled totalGold    xp  
0            81      5567  8821  
1             2      5415  5186  
2            95      4324  6550  
3           109      7532  5713  
4            25      4546  3966  
5           102      4929  6556  
6            13      5471  5626  
7            90      4558  6457  
8            35      3492  4091  
9            29      3462  4742

In [9]:
#Para leer todos los archivos JSON de una carpeta

def combine_dataframes(json_folder):
    # Obtener la lista de archivos JSON en la carpeta
    json_files = [file for file in os.listdir(json_folder) if file.endswith('.json')]

    # Crear una lista para almacenar los DataFrames de cada archivo
    dfs = []
    
    

    # Recorrer cada archivo JSON y combinar los datos en un DataFrame
    for json_file in json_files:
        
        # Reiniciar el contador para cada archivo JSON
        player_id_counter = 0
        
        json_path = os.path.join(json_folder, json_file)
        df = pd.read_json(json_path)

        # Verificar la estructura del archivo JSON
        if "info" in df and "frames" in df["info"]:
            frames = df["info"]["frames"]
            if len(frames) > 15 and "participantFrames" in frames[15]:
                participant_frames = frames[15]["participantFrames"]
                if participant_frames:
                    df_loop = pd.DataFrame(participant_frames).transpose()[["championStats", "damageStats", "jungleMinionsKilled", "minionsKilled", "totalGold", "xp"]].reset_index(drop=True)
                    damage_stats = df_loop["damageStats"]
                    champion_stats = df_loop["championStats"]
                    damage_stats_expanded = pd.json_normalize(damage_stats)
                    champion_stats_expanded = pd.json_normalize(champion_stats)
                    damage_stats_expanded = damage_stats_expanded.reset_index(drop=True)
                    champion_stats_expanded = champion_stats_expanded.reset_index(drop=True)

                    combined_df = df_loop.join(champion_stats_expanded)
                    combined_df = combined_df.join(damage_stats_expanded).drop(columns=["championStats", "damageStats"])
                    
                    # Agregar la columna "player_id" con valores secuenciales para cada archivo JSON
                    combined_df["player_id"] = range(player_id_counter, player_id_counter + len(combined_df))
                    
                    # Incrementar el contador de player_id para el siguiente archivo JSON
                    player_id_counter += len(combined_df)
                    
                    # Obtener el valor de matchId del archivo JSON
                    match_id = df["metadata"]["matchId"]
                    
                    # Repetir el valor de matchId en las 10 filas del DataFrame actual
                    combined_df["matchId"] = match_id

                    dfs.append(combined_df)  # Agregar el DataFrame combinado a la lista

    # Combinar todos los DataFrames en uno solo
    combined_df = pd.concat(dfs, ignore_index=True)

    return combined_df

# Ruta de la carpeta que contiene los archivos JSON
json_folder = 'data/IRON/Timeline/Partidas'

# Llamar a la función para combinar los DataFrames
combined_df = combine_dataframes(json_folder)




In [10]:
"""#usar esto para leer el archivo de csv:
combined_df = pd.read_csv("data/IRON/Timeline/PartidasIronTimeline.csv")"""

'#usar esto para leer el archivo de csv:\ncombined_df = pd.read_csv("data/IRON/Timeline/PartidasIronTimeline.csv")'

In [11]:
combined_df

jungleMinionsKilled minionsKilled totalGold    xp  abilityHaste  \
0                       4            87      5753  7145           0.0   
1                      60             8      5759  5296           0.0   
2                       0            78      4508  6734           0.0   
3                       0            75      6480  5214           0.0   
4                       0            24      4746  4606           0.0   
...                   ...           ...       ...   ...           ...   
47045                   4            87      4570  7947           0.0   
47046                  60            16      5621  5078           0.0   
47047                   4            73      6166  6003           0.0   
47048                   8            78      4723  4832           0.0   
47049                   0            15      3909  4606           0.0   

       abilityPower  armor  armorPen  armorPenPercent  attackDamage  ...  \
0                 0    121         0                0           183  ...   
1                 0     73         0               10           164  ...   
2               112     64         0                0            82  ...   
3                 0     63         0                0           173  ...   
4                 0    127         0                0            92  ...   
...             ...    ...       ...              ...           ...  ...   
47045             0     75         0                0           153  ...   
47046             0     72         0                0           155  ...   
47047             0     61         0                0           196  ...   
47048             0     58         0                0           129  ...   
47049            23    105         0                0            74  ...   

       physicalDamageDoneToChampions  physicalDamageTaken  totalDamageDone  \
0                               3375                 4744            56079   
1                               5737                 6219            64422   
2                                446                 1828            41228   
3                               7203                 2135            41659   
4                               1344                 3110            13656   
...                              ...                  ...              ...   
47045                            990                 5530            39856   
47046                           2852                 7352            72486   
47047                           7948                 5402            42117   
47048                           3325                 2746            43180   
47049                            354                 4995            11429   

       totalDamageDoneToChampions  totalDamageTaken  trueDamageDone  \
0                            4820              5798            8492   
1                            6218              9646           14786   
2                            5862              8329              26   
3                            7888              3698            4099   
4                            3529              5639            3098   
...                           ...               ...             ...   
47045                        1792              5935            4955   
47046                        5316              9749           13369   
47047                        8322              8476             374   
47048                        3998              5023             398   
47049                        2934              7396            1773   

       trueDamageDoneToChampions  trueDamageTaken  player_id         matchId  
0                           1444                0          0  LA2_1304858815  
1                            271               20          1  LA2_1304858815  
2                             26              423          2  LA2_1304858815  
3                            375              116          3  LA2_1304858815  
4                              

In [48]:
#Definimos los eventos de interés
look_events=["CHAMPION_SPECIAL_KILL","CHAMPION_KILL","ELITE_MONSTER_KILL","BUILDING_KILL"]


folder_path = "data/IRON/Timeline/Partidas/" #Change to your folder path

def find_indices(data):
    monster_indices = []
    for index, item in enumerate(data):
        if item.get('type') in look_events:
            monster_indices.append(index)
    return monster_indices

def get_events(json_file):
    elements_filtered = []
    for i in range(16):
        try:
            events = json_file["info"]["frames"][i]["events"]
        except IndexError:
            break
        monster_indices = find_indices(events)
        if monster_indices:
            new_elements = [events[e] for e in monster_indices]
            elements_filtered.extend(new_elements)

    events_filtered = pd.DataFrame(elements_filtered)
    return events_filtered


def transform_events(json_file):
    required_columns = ["killerId", "type", "killType", "monsterSubType", "monsterType", "towerType"]

    events = get_events(json_file)

    missing_columns = [col for col in required_columns if col not in events.columns]

    for column in missing_columns:
        events[column] = np.nan

    events = events[required_columns]
    events = events[events["killerId"] != 0]

    events.loc[events["monsterType"] == "DRAGON", "monsterType"] = events.loc[events["monsterType"] == "DRAGON", "monsterSubType"]

    events = events.drop(columns=["monsterSubType"])

    events["kills"] = (events["type"] == "CHAMPION_KILL").astype(int)

    one_hot_encoded = pd.get_dummies(events[['killType', "monsterType", "towerType"]])

    events_encoded = pd.concat([events[['killerId', "kills"]], one_hot_encoded], axis=1)
    
    if 'killType' in events_encoded.columns:
        events_encoded.drop(columns=['killType'], inplace=True)
    if 'monsterType' in events_encoded.columns:
        events_encoded.drop(columns=['monsterType'], inplace=True)
    if 'towerType' in events_encoded.columns:
        events_encoded.drop(columns=['towerType'], inplace=True)
    
    events_encoded = events_encoded.groupby("killerId").sum().reset_index()

    events_encoded["killerId"] = events_encoded["killerId"] - 1

    events_encoded = events_encoded.groupby("killerId").sum().reset_index()

    conditions = [
        (events_encoded['killerId'] >= 0) & (events_encoded['killerId'] <= 4),
        (events_encoded['killerId'] >= 5) & (events_encoded['killerId'] <= 9)
    ]
    values = [100, 200]

    events_encoded['team'] = np.select(conditions, values, default=0)

    events_encoded = events_encoded.groupby("team").sum().reset_index().drop(columns=["killerId"])

    events_encoded["matchId"] = json_file["metadata"]["matchId"]
    
    last_event = json_file["info"]["frames"][-1]["events"][-1]
    events_encoded["target"] = events_encoded["team"].apply(lambda x: 1 if x == last_event.get("winningTeam") else 0)
    
    events_encoded = events_encoded.drop(columns=["team"])

    return events_encoded


all_events = None

for filename in os.listdir(folder_path):
    if filename.endswith('.json'):
        file_path = os.path.join(folder_path, filename)
        
        json_file = pd.read_json(file_path)
                        
        if all_events is None:
            all_events = transform_events(json_file)
        else:
            all_events = pd.concat([all_events, transform_events(json_file)], ignore_index=True)
     
columns_to_convert = all_events.columns[~all_events.columns.isin(['matchId',"target"])]   
    
all_events[columns_to_convert] = all_events[columns_to_convert].fillna(0).astype(int) 

#All events es el df de los eventos definidos agrupados por partida y 2 equipos
all_events






kills  killType_KILL_FIRST_BLOOD  killType_KILL_MULTI  \
0        18                          1                    1   
1         7                          0                    0   
2        21                          1                    1   
3        11                          0                    1   
4         9                          0                    0   
...     ...                        ...                  ...   
9595      8                          1                    0   
9596     10                          0                    0   
9597      6                          1                    2   
9598      7                          0                    0   
9599     13                          1                    1   

      monsterType_FIRE_DRAGON  towerType_OUTER_TURRET         matchId  target  \
0                           1                       1  LA2_1304858815       1   
1                           0                       0  LA2_1304858815       0   
2                           0                       2  LA2_1291817117       1   
3                           0                       0  LA2_1291817117       0   
4                           0                       1  LA2_1182343361       0   
...                       ...                     ...             ...     ...   
9595                        0                       0  LA2_1200889925       1   
9596                        0                       1  LA2_1263695332       1   
9597                        0                       0  LA2_1263695332       0   
9598                        0                       0  LA2_1253811110       0   
9599                        0                       0  LA2_1253811110       1   

      monsterType_AIR_DRAGON  monsterType_RIFTHERALD  \
0                          0                       0   
1                          0                       0   
2                          0                       1   
3                          1                       0   
4                          1                       1   
...                      ...                     ...   
9595                       0                       1   
9596                       0                       0   
9597                       0                       1   
9598                       0                       0   
9599                       1                       1   

      monsterType_HEXTECH_DRAGON  monsterType_EARTH_DRAGON  \
0                              0                         0   
1                              0                         0   
2                              0                         0   
3                              0                         0   
4                              0                         0   
...                          ...                       ...   
9595                           0                         0   
9596                           1                         0   
9597                           0                         0   
9598                           1                         0   
9599                           0                         0   

      monsterType_WATER_DRAGON  monsterType_CHEMTECH_DRAGON  \
0                            0                            0   
1                            0                            0   
2                            0                            0   
3                            0                            0   
4                            0                            0   
...                        ...                          ...   
9595                         0                            0   
9596                         0                            0   
9597                         0                            1   
9598                         0                            0   
9599                         0                            0   

      towerType_INNER_TURRET  killType_KILL_ACE  towerType_BASE_TURRET  \
0                          

In [49]:
all_events.to_excel("data/IRON/Timeline/all_events.xlsx")

In [22]:
df_trabajo = combined_df.copy()
df_trabajo

jungleMinionsKilled minionsKilled totalGold    xp  abilityHaste  \
0                       4            87      5753  7145           0.0   
1                      60             8      5759  5296           0.0   
2                       0            78      4508  6734           0.0   
3                       0            75      6480  5214           0.0   
4                       0            24      4746  4606           0.0   
...                   ...           ...       ...   ...           ...   
47045                   4            87      4570  7947           0.0   
47046                  60            16      5621  5078           0.0   
47047                   4            73      6166  6003           0.0   
47048                   8            78      4723  4832           0.0   
47049                   0            15      3909  4606           0.0   

       abilityPower  armor  armorPen  armorPenPercent  attackDamage  ...  \
0                 0    121         0                0           183  ...   
1                 0     73         0               10           164  ...   
2               112     64         0                0            82  ...   
3                 0     63         0                0           173  ...   
4                 0    127         0                0            92  ...   
...             ...    ...       ...              ...           ...  ...   
47045             0     75         0                0           153  ...   
47046             0     72         0                0           155  ...   
47047             0     61         0                0           196  ...   
47048             0     58         0                0           129  ...   
47049            23    105         0                0            74  ...   

       physicalDamageDoneToChampions  physicalDamageTaken  totalDamageDone  \
0                               3375                 4744            56079   
1                               5737                 6219            64422   
2                                446                 1828            41228   
3                               7203                 2135            41659   
4                               1344                 3110            13656   
...                              ...                  ...              ...   
47045                            990                 5530            39856   
47046                           2852                 7352            72486   
47047                           7948                 5402            42117   
47048                           3325                 2746            43180   
47049                            354                 4995            11429   

       totalDamageDoneToChampions  totalDamageTaken  trueDamageDone  \
0                            4820              5798            8492   
1                            6218              9646           14786   
2                            5862              8329              26   
3                            7888              3698            4099   
4                            3529              5639            3098   
...                           ...               ...             ...   
47045                        1792              5935            4955   
47046                        5316              9749           13369   
47047                        8322              8476             374   
47048                        3998              5023             398   
47049                        2934              7396            1773   

       trueDamageDoneToChampions  trueDamageTaken  player_id         matchId  
0                           1444                0          0  LA2_1304858815  
1                            271               20          1  LA2_1304858815  
2                             26              423          2  LA2_1304858815  
3                            375              116          3  LA2_1304858815  
4                              

In [13]:
# Especificar la ruta y el nombre del archivo de Excel
ruta_archivo = 'data/IRON/Timeline/df_trabajo.xlsx'

# Guardar el DataFrame en un archivo de Excel
df_trabajo.to_excel(ruta_archivo, index=False)

In [14]:
combined_df.to_csv('PartidasIronTimeline.csv', index=False)

In [15]:
"""champion_stats_cl = list(df_test["championStats"][0].keys())
damage_stats_cl = list(df_test["damageStats"][0].keys())
print(champion_stats_cl)
print(damage_stats_cl)"""

'champion_stats_cl = list(df_test["championStats"][0].keys())\ndamage_stats_cl = list(df_test["damageStats"][0].keys())\nprint(champion_stats_cl)\nprint(damage_stats_cl)'

In [16]:
#Definimos función que nos retorna un diciconario
def return_dict(diccionario, colum_names):
    lista = list(diccionario.values())
    return pd.Series(lista, index= colum_names)

In [17]:
"""df_test[champion_stats_cl] = df_test['championStats'].apply(lambda x :  return_dict(x, champion_stats_cl))
df_test[damage_stats_cl] = df_test['damageStats'].apply(lambda x :  return_dict(x, damage_stats_cl))
df_test"""

"df_test[champion_stats_cl] = df_test['championStats'].apply(lambda x :  return_dict(x, champion_stats_cl))\ndf_test[damage_stats_cl] = df_test['damageStats'].apply(lambda x :  return_dict(x, damage_stats_cl))\ndf_test"

In [20]:
"""# Lee el archivo de Excel
excel_info = pd.read_excel('participant.xlsx', sheet_name='Sheet1')

# Aplica la condición y obtén la columna como lista ----> seleccionar las columnas del excel que establecimos como "drop"
drop_columns = excel_info.loc[excel_info['Operación'] == 'drop']['feature'].tolist()

sum_columns = excel_info.loc[excel_info['Operación'] == 'sum']['feature'].tolist()

average_columns = excel_info.loc[excel_info['Operación'] == 'average']['feature'].tolist()

bool_columns = excel_info.loc[excel_info['Operación'] == 'bool']['feature'].tolist()"""


'# Lee el archivo de Excel\nexcel_info = pd.read_excel(\'participant.xlsx\', sheet_name=\'Sheet1\')\n\n# Aplica la condición y obtén la columna como lista ----> seleccionar las columnas del excel que establecimos como "drop"\ndrop_columns = excel_info.loc[excel_info[\'Operación\'] == \'drop\'][\'feature\'].tolist()\n\nsum_columns = excel_info.loc[excel_info[\'Operación\'] == \'sum\'][\'feature\'].tolist()\n\naverage_columns = excel_info.loc[excel_info[\'Operación\'] == \'average\'][\'feature\'].tolist()\n\nbool_columns = excel_info.loc[excel_info[\'Operación\'] == \'bool\'][\'feature\'].tolist()'

In [27]:
operaciones = {
    'sum': lambda x: x.sum(),
    'average': lambda x: x.mean(),
    'bool': lambda x: x.any()
}



    
#Caso se lea desde un excel y definamos en el mismo la agrupación de cada columna
"""for columna in reduced_df.columns:
    if columna in drop_columns:
        continue  # Saltar columna si se encuentra en drop_columns
    operacion = excel_info.loc[excel_info['feature'] == columna, 'Operación'].iloc[0]
    funcion = operaciones.get(operacion)
    
    if funcion is None:
        # Operación no encontrada en el diccionario, manejar el caso según sea necesario
        resultado = None  # Otra asignación o manejo adecuado
    else:
        resultado = funcion(reduced_df[columna])
    
    df_transformado[columna] = resultado"""
    


# Define una función predeterminada que no hace ningún cálculo
def no_operation(x):
    return np.nan

# Definir una función de operación que suma los valores de una columna
def sum_operation(column):
    return column.sum()

df_transformado = pd.DataFrame(columns=df_trabajo.columns.drop(['player_id']))

group_size = 5
num_rows = len(df_trabajo)

#Caso se quiera trabajar leyendo la info sobre operaciones para agrupación de columnas detalladas en excel

"""for i in range(0, num_rows, group_size):
    # Obetener  el grupo de filas actual (5 y 5)
    group = df_trabajo.iloc[i:i+group_size]
    
    # Aplica la operación determinada para el grupo actual  
    group_result = group.apply(lambda column: operaciones.get(excel_info.loc[excel_info['feature'] == column.name, 'Operación'].iloc[0], no_operation)(column))
    
   # Agrega el resultado del grupo al DataFrame transformado
    df_transformado = df_transformado.append(group_result, ignore_index=True)"""

# Definir una función de operación que suma los valores de una columna
def sum_operation(column):
    return column.sum()    

for i in range(0, num_rows, group_size):
    # Obtener el grupo de filas actual (tamaño de grupo definido por group_size)
    group = df_trabajo.iloc[i:i+group_size]
    
    # Excluir la columna 'matchID' del cálculo de suma
    group_without_matchID = group.drop(columns=['matchId'])
    
    # Aplicar la operación de suma para el grupo actual (excluyendo 'matchID')
    group_result = group_without_matchID.apply(sum_operation, axis=0)
    
    # Agregar el primer valor de 'matchID' al DataFrame transformado
    group_result['matchId'] = group['matchId'].iloc[0]
    
    # Agregar el resultado del grupo al DataFrame transformado
    df_transformado = df_transformado.append(group_result, ignore_index=True)




/tmp/ipykernel_990/4261132924.py:70: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_transformado = df_transformado.append(group_result, ignore_index=True)
/tmp/ipykernel_990/4261132924.py:70: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_transformado = df_transformado.append(group_result, ignore_index=True)
/tmp/ipykernel_990/4261132924.py:70: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_transformado = df_transformado.append(group_result, ignore_index=True)
/tmp/ipykernel_990/4261132924.py:70: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_transformado = df_transformado.append(group_result, ignore_index=True)
/tmp/ipykernel_9

In [45]:
#df_transformado es la agrupación de las partidas por timeline, el criterio para la agrupación es por equipos, sumando las estadísticas de jugadores individuales.
df_transformado.drop(columns="player_id", inplace=True)
df_transformado

jungleMinionsKilled  minionsKilled  totalGold       xp  abilityHaste  \
0                    64.0          272.0    27246.0  28995.0           0.0   
1                    64.0          218.0    20113.0  25487.0           0.0   
2                    56.0          267.0    29683.0  28585.0           0.0   
3                    72.0          230.0    22777.0  23797.0           0.0   
4                    62.0          207.0    22903.0  24877.0           0.0   
...                   ...            ...        ...      ...           ...   
9405                 71.0          262.0    22700.0  28663.0           0.0   
9406                 90.0          282.0    24601.0  29757.0           0.0   
9407                 72.0          297.0    23176.0  28000.0           0.0   
9408                 68.0          271.0    22623.0  27131.0           0.0   
9409                 76.0          269.0    24989.0  28466.0           0.0   

      abilityPower  armor  armorPen  armorPenPercent  attackDamage  ...  \
0            112.0  448.0       0.0             10.0         694.0  ...   
1            409.0  321.0       0.0              0.0         500.0  ...   
2            101.0  387.0       0.0              0.0         681.0  ...   
3              0.0  336.0       0.0             10.0         893.0  ...   
4            120.0  376.0       0.0              4.0         639.0  ...   
...            ...    ...       ...              ...           ...  ...   
9405         166.0  382.0       0.0              0.0         547.0  ...   
9406         233.0  667.0       0.0              0.0         502.0  ...   
9407         239.0  418.0       0.0              0.0         519.0  ...   
9408         243.0  347.0       0.0             20.0         519.0  ...   
9409          23.0  371.0       0.0              0.0         707.0  ...   

      physicalDamageDone  physicalDamageDoneToChampions  physicalDamageTaken  \
0               146733.0                        18105.0              18036.0   
1                65718.0                         5437.0              26723.0   
2               174956.0                        18533.0              35011.0   
3               143631.0                        21138.0              31607.0   
4               115158.0                        18065.0              18464.0   
...                  ...                            ...                  ...   
9405            117136.0                         8506.0              22168.0   
9406            155194.0                        15358.0              20976.0   
9407             91301.0                         9418.0              25105.0   
9408            108266.0                        12754.0              26744.0   
9409            151240.0                        15469.0              26025.0   

      totalDamageDone  totalDamageDoneToChampions  totalDamageTaken  \
0            217044.0                     28317.0           33110.0   
1            172483.0                     19981.0           38499.0   
2            234137.0                     32623.0           38141.0   
3            178129.0                     23374.0           47443.0   
4            168989.0                     28981.0           42805.0   
...               ...                         ...               ...   
9405         202081.0                     21339.0           29598.0   
9406         248452.0                     30555.0           31476.0   
9407         205113.0                     19540.0           41243.0   
9408         202587.0                     22711.0           34707.0   
9409         209068.0                     22362.0           36579.0   

      trueDamageDone  trueDamageDoneToChampions  trueDamageTaken  \
0            30501.0                     2116.0            825.0   
1            15457.0                      825.0           2116.0   
2            31360.0                     3078.0            848.0   
3            18295.0                      850.0           3077.0   
4            1

In [29]:

df_transformado.to_excel("data/IRON/Timeline/Partidas/df_transformado.xlsx")

In [39]:
"""columnas_tipo = {
    int: sum_columns,
    float: average_columns,
    bool: bool_columns
}

for tipo, columnas in columnas_tipo.items():
    for columna in columnas:
        df_trabajo[columna] = df_trabajo[columna].astype(tipo)"""
df_transformado

jungleMinionsKilled  minionsKilled  totalGold       xp  abilityHaste  \
0                    64.0          272.0    27246.0  28995.0           0.0   
1                    64.0          218.0    20113.0  25487.0           0.0   
2                    56.0          267.0    29683.0  28585.0           0.0   
3                    72.0          230.0    22777.0  23797.0           0.0   
4                    62.0          207.0    22903.0  24877.0           0.0   
...                   ...            ...        ...      ...           ...   
9405                 71.0          262.0    22700.0  28663.0           0.0   
9406                 90.0          282.0    24601.0  29757.0           0.0   
9407                 72.0          297.0    23176.0  28000.0           0.0   
9408                 68.0          271.0    22623.0  27131.0           0.0   
9409                 76.0          269.0    24989.0  28466.0           0.0   

      abilityPower  armor  armorPen  armorPenPercent  attackDamage  ...  \
0            112.0  448.0       0.0             10.0         694.0  ...   
1            409.0  321.0       0.0              0.0         500.0  ...   
2            101.0  387.0       0.0              0.0         681.0  ...   
3              0.0  336.0       0.0             10.0         893.0  ...   
4            120.0  376.0       0.0              4.0         639.0  ...   
...            ...    ...       ...              ...           ...  ...   
9405         166.0  382.0       0.0              0.0         547.0  ...   
9406         233.0  667.0       0.0              0.0         502.0  ...   
9407         239.0  418.0       0.0              0.0         519.0  ...   
9408         243.0  347.0       0.0             20.0         519.0  ...   
9409          23.0  371.0       0.0              0.0         707.0  ...   

      physicalDamageDoneToChampions  physicalDamageTaken  totalDamageDone  \
0                           18105.0              18036.0         217044.0   
1                            5437.0              26723.0         172483.0   
2                           18533.0              35011.0         234137.0   
3                           21138.0              31607.0         178129.0   
4                           18065.0              18464.0         168989.0   
...                             ...                  ...              ...   
9405                         8506.0              22168.0         202081.0   
9406                        15358.0              20976.0         248452.0   
9407                         9418.0              25105.0         205113.0   
9408                        12754.0              26744.0         202587.0   
9409                        15469.0              26025.0         209068.0   

      totalDamageDoneToChampions  totalDamageTaken  trueDamageDone  \
0                        28317.0           33110.0         30501.0   
1                        19981.0           38499.0         15457.0   
2                        32623.0           38141.0         31360.0   
3                        23374.0           47443.0         18295.0   
4                        28981.0           42805.0         19367.0   
...                          ...               ...             ...   
9405                     21339.0           29598.0         18298.0   
9406                     30555.0           31476.0         40015.0   
9407                     19540.0           41243.0         36911.0   
9408                     22711.0           34707.0         26063.0   
9409                     22362.0           36579.0         20869.0   

      trueDamageDoneToChampions  trueDamageTaken         matchId  player_id  
0                        2116.0            825.0  LA2_1304858815       10.0  
1                         825.0           2116.0  LA2_1304858815       35.0  
2                        3078.0            848.0  LA2_1291817117       10.0  
3                         850.0           3077.0  LA2_1291817117       35.0  
4           

In [46]:


# Seleccionar todas las columnas excepto "matchId"
columnas_no_matchId = df_transformado.columns[df_transformado.columns != "matchId"]

# Seleccionar solo las columnas numéricas
columnas_numericas = df_transformado.select_dtypes(include=[np.number])

# Crear un nuevo DataFrame vacío con la misma columna "matchId" y las columnas numéricas
df_partida_diff = pd.DataFrame(columns=["matchId"] + list(columnas_numericas.columns))

# Obtener el número total de filas en df_trabajo
total_filas = columnas_numericas.shape[0]

# Iterar a través de las filas de columnas_numericas
for i in range(0, total_filas - 1, 2):
    # Obtener las dos filas a restar
    fila1 = columnas_numericas.iloc[i]
    fila2 = columnas_numericas.iloc[i+1]
    
    # Calcular la resta de las dos filas
    resta_filas = fila1 - fila2
    
    # Agregar la resta al nuevo DataFrame df_partida_diff
    df_partida_diff = df_partida_diff.append(resta_filas, ignore_index=True)

# Asignar el primer valor de las columnas booleanas en cada fila del nuevo DataFrame
for columna in df_transformado.select_dtypes(include=[bool]):
    df_partida_diff[columna] = df_transformado[columna].iloc[::2].reset_index(drop=True)

# Asignar el primer valor de la columna "matchId" en cada fila del nuevo DataFrame
df_partida_diff["matchId"] = df_transformado["matchId"].iloc[::2].reset_index(drop=True)



/tmp/ipykernel_990/1866011101.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_partida_diff = df_partida_diff.append(resta_filas, ignore_index=True)
/tmp/ipykernel_990/1866011101.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_partida_diff = df_partida_diff.append(resta_filas, ignore_index=True)
/tmp/ipykernel_990/1866011101.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_partida_diff = df_partida_diff.append(resta_filas, ignore_index=True)
/tmp/ipykernel_990/1866011101.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_partida_diff = df_partida_diff.append(resta_filas, ignore_index=True)
/tmp/ipykernel_990/1

In [55]:
all_events.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9600 entries, 0 to 9599
Data columns (total 17 columns):
 #   Column                       Non-Null Count  Dtype 
---  ------                       --------------  ----- 
 0   kills                        9600 non-null   int64 
 1   killType_KILL_FIRST_BLOOD    9600 non-null   int64 
 2   killType_KILL_MULTI          9600 non-null   int64 
 3   monsterType_FIRE_DRAGON      9600 non-null   int64 
 4   towerType_OUTER_TURRET       9600 non-null   int64 
 5   matchId                      9600 non-null   object
 6   target                       9600 non-null   int64 
 7   monsterType_AIR_DRAGON       9600 non-null   int64 
 8   monsterType_RIFTHERALD       9600 non-null   int64 
 9   monsterType_HEXTECH_DRAGON   9600 non-null   int64 
 10  monsterType_EARTH_DRAGON     9600 non-null   int64 
 11  monsterType_WATER_DRAGON     9600 non-null   int64 
 12  monsterType_CHEMTECH_DRAGON  9600 non-null   int64 
 13  towerType_INNER_TURRET       9600

In [70]:
#Aplica lo mismo pero para all_events df


# Seleccionar todas las columnas excepto "matchId y"
columnas_no_matchId = all_events.columns[~ all_events.columns.isin(["matchId", "target"])]

# Seleccionar solo las columnas numéricas
columnas_numericas = all_events.select_dtypes(include=[np.number]).drop(columns = "target")

# Crear un nuevo DataFrame vacío con la misma columna "matchId, target" y las columnas numéricas
all_events_diff = pd.DataFrame(columns=["matchId", "target"] + list(columnas_numericas.columns))

# Obtener el número total de filas en df_trabajo
total_filas = columnas_numericas.shape[0]

# Iterar a través de las filas de columnas_numericas
for i in range(0, total_filas - 1, 2):
    # Obtener las dos filas a restar
    fila1 = columnas_numericas.iloc[i]
    fila2 = columnas_numericas.iloc[i+1]
    
    # Calcular la resta de las dos filas
    resta_filas = fila1 - fila2
    
    # Agregar la resta al nuevo DataFrame df_partida_diff
    all_events_diff = all_events_diff.append(resta_filas, ignore_index=True)

# Asignar el primer valor de las columnas booleanas en cada fila del nuevo DataFrame
for columna in all_events.select_dtypes(include=[bool]):
    all_events_diff[columna] = all_events[columna].iloc[::2].reset_index(drop=True)

# Asignar el primer valor de la columna "matchId" en cada fila del nuevo DataFrame
all_events_diff["matchId"] = all_events["matchId"].iloc[::2].reset_index(drop=True)

# Asignar el primer valor de la columna "target" en cada fila del nuevo DataFrame
all_events_diff["target"] = all_events["target"].iloc[::2].reset_index(drop=True)


/tmp/ipykernel_990/193335955.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  all_events_diff = all_events_diff.append(resta_filas, ignore_index=True)
/tmp/ipykernel_990/193335955.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  all_events_diff = all_events_diff.append(resta_filas, ignore_index=True)
/tmp/ipykernel_990/193335955.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  all_events_diff = all_events_diff.append(resta_filas, ignore_index=True)
/tmp/ipykernel_990/193335955.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  all_events_diff = all_events_diff.append(resta_filas, ignore_index=True)
/tmp/ipykernel_990/19333

In [74]:
all_events_diff["target"].value_counts()

1    2428
0    2372
Name: target, dtype: int64

In [47]:
df_partida_diff

matchId  jungleMinionsKilled  minionsKilled  totalGold      xp  \
0     LA2_1304858815                  0.0           54.0     7133.0  3508.0   
1     LA2_1291817117                -16.0           37.0     6906.0  4788.0   
2     LA2_1182343361                 13.0          -37.0    -1391.0 -1522.0   
3     LA2_1304108873                  0.0            0.0       44.0  -212.0   
4     LA2_1200306843                  8.0           -5.0      836.0  -672.0   
...              ...                  ...            ...        ...     ...   
4700  LA2_1248445548                -17.0          -92.0   -14087.0 -9431.0   
4701  LA2_1280271305                -10.0           52.0     4769.0  3964.0   
4702  LA2_1200889925                 -6.0            9.0     -386.0  -578.0   
4703  LA2_1263695332                 18.0          -15.0     1425.0  1757.0   
4704  LA2_1253811110                 -8.0            2.0    -2366.0 -1335.0   

      abilityHaste  abilityPower  armor  armorPen  armorPenPercent  ...  \
0              0.0        -297.0  127.0       0.0             10.0  ...   
1              0.0         101.0   51.0       0.0            -10.0  ...   
2              0.0        -252.0   63.0       0.0              4.0  ...   
3              0.0          34.0   62.0       0.0              0.0  ...   
4              0.0          -2.0  -34.0       0.0              0.0  ...   
...            ...           ...    ...       ...              ...  ...   
4700           0.0        -248.0 -119.0       0.0            -20.0  ...   
4701           0.0         114.0 -171.0       0.0             15.0  ...   
4702           0.0         -93.0  -47.0       0.0              0.0  ...   
4703           0.0          -6.0  249.0       0.0              0.0  ...   
4704           0.0         220.0  -24.0       0.0             20.0  ...   

      magicDamageTaken  physicalDamageDone  physicalDamageDoneToChampions  \
0               4589.0             81015.0                        12668.0   
1             -10473.0             31325.0                        -2605.0   
2              15035.0             45467.0                        11234.0   
3               5696.0             12195.0                         3364.0   
4               3588.0             11009.0                         3747.0   
...                ...                 ...                            ...   
4700            5890.0            -35295.0                        -1958.0   
4701            -170.0             32462.0                         5672.0   
4702            6627.0            -27370.0                         2698.0   
4703           -4726.0             63893.0                         5940.0   
4704           -2497.0            -42974.0                        -2715.0   

      physicalDamageTaken  totalDamageDone  totalDamageDoneToChampions  \
0                 -8687.0          44561.0                      8336.0   
1                  3404.0          56008.0                      9249.0   
2                -10385.0           2740.0                     -1531.0   
3                 -4736.0         -16390.0                     -5771.0   
4                  -194.0          -1473.0                      -312.0   
...                   ...              ...                         ...   
4700               1788.0         -67760.0                     -6737.0   
4701              -5484.0          29691.0                      7605.0   
4702              -2311.0         -27856.0                     -3242.0   
4703              -4129.0          43339.0                     11015.0   
4704                719.0          -6481.0                       349.0   

      totalDamageTaken  trueDamageDone  trueDamageDoneToChampions  \
0              -5389.0         15044.0                     1291.0   
1              -9302.0         13065.0                     2228.0   
2               2082.0          9001.0                     2565.0   
3               2595.0         -1336.0                    -1635.0   
4   

In [ ]:
# Mostrar el nuevo DataFrame
df_partida_agrupada

In [ ]:
df_partida_agrupada.to_csv("data/IRON/df_partida_agrupada.csv")

In [ ]:
columnas_tipo = {
    int: sum_columns,
    float: average_columns,
    bool: bool_columns
}

for tipo, columnas in columnas_tipo.items():
    for columna in columnas:
        df_trabajo[columna] = df_trabajo[columna].astype(tipo)
        


In [ ]:
df_trabajo.info()

In [ ]:
# Counting the number of NaN for each column
df_trabajo.isnull().sum().sort_values(ascending=False) 

In [ ]:
df_trabajo.info()

In [ ]:
df_trabajo.describe()


In [ ]:
correlation_matrix = df_trabajo.corr()
print(correlation_matrix)


In [ ]:
categorical_features = bool_columns

#Build functions
def duplicates(df):
    print(f"Duplicates droped: {df.duplicated().sum()}")
    df = df.drop_duplicates()
    return df

def missing_data_num(df_num): #TBD if needed
    return df_num

def missing_data_cat(df_cat):#TBD if needed
    return df_cat

def scale(df_num):
    #Standard or Robust if there are many otliers
    scaler = RobustScaler()
    column_names = df_num.columns.tolist()
    df_num = scaler.fit_transform(df_num)
    df_scaled = pd.DataFrame(df_num, columns=column_names)
    return df_scaled


# Start script
"""






corr_threshold = 0.9 #To be adjusted
corr_over_df = corr_df[corr_df["absolute_correlation"] >= corr_threshold]
irrelevant_features = list(set(corr_over_df["feature_2"]))
df = df.drop(columns=[irrelevant_features],inplace = True)"""

In [ ]:
#Separate categorical features
df_cat = df_trabajo[categorical_features]

#Remove missing data from categorical features
df_cat = missing_data_cat(df_cat)



In [ ]:
#Separate numerical features
df_num = df_trabajo.drop(columns=categorical_features)
#Transform numerical features
df_num = missing_data_num(df_num)
#Apply scaler to df_num
df_num_scaled = scale(df_num)
df_num_scaled


In [ ]:

#Concat categorical and numerical processed features
df_preprocessed = pd.concat([df_num_scaled,df_cat],axis=1)
df_preprocessed

In [ ]:
#correlation analysis to drop features that have high correlation
correlation_matrix = df_preprocessed.corr()
column_names = correlation_matrix.columns
correlation_matrix

In [ ]:
#pd.set_option('display.max_rows', None)
corr_df = correlation_matrix.stack().reset_index()
corr_df.columns = ['feature_1','feature_2', 'correlation']
no_self_correlation = (corr_df['feature_1'] != corr_df['feature_2'])
corr_df = corr_df[no_self_correlation]
corr_df['absolute_correlation'] = np.abs(corr_df['correlation'])
corr_df.sort_values(by="absolute_correlation", ascending=False).round(4).head(5) #Remove comment to show df



In [ ]:

df_preprocessed["win"].iloc[::2].value_counts()

In [ ]:
model = Logi

In [ ]:
corr_df.to_excel("correlation.")